# inference_bert_synthsts.ipynb



In [ ]:
!pip install sentence-transformers transformers accelerate -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 156.5/156.5 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 280.0/280.0 kB 18.7 MB/s eta 0:00:00


In [ ]:
model_name = "BEE-spoke-data/bert-plus-L8-v1.0-syntheticSTS-4k" # @param {type:"string"}
#@markdown > try replacing the model with `sentence-transformers/all-mpnet-base-v2` and re-run to see the difference
model_name

'BEE-spoke-data/bert-plus-L8-v1.0-syntheticSTS-4k'

In [ ]:
import torch
from sentence_transformers import SentenceTransformer

torch.cuda.empty_cache()
model = SentenceTransformer(
    model_name,
)
model.eval()

texts = ["this is a document", "another document goes here", "yet another document"]
batch_embeddings = model.encode(
    texts,
    batch_size=2,
    convert_to_tensor=True,
    show_progress_bar=True,
    normalize_embeddings=True,
)

print(f"Batch embeddings shape: {batch_embeddings.shape}")
# Batch embeddings shape: torch.Size([3, 768])

modules.json:   0%|          | 0.00/229 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/171 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/3.28k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/54.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/662 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/296 [00:00<?, ?B/s]

Batches:   0%|          | 0/2 [00:00<?, ?it/s]

Batch embeddings shape: torch.Size([3, 768])


In [ ]:
batch_embeddings

tensor([[ 7.8719e-02, -1.9018e-02,  1.5204e-02,  ...,  2.7744e-03,
          7.6688e-03,  3.1916e-02],
        [ 7.8842e-02, -1.4545e-02, -3.7121e-03,  ...,  1.8336e-02,
         -1.2331e-02,  2.9763e-02],
        [ 8.6998e-02, -1.4927e-02,  8.7610e-05,  ...,  2.2486e-02,
         -3.2547e-03,  4.1723e-02]], device='cuda:0')

## load data

In [ ]:
from pathlib import Path
import pandas as pd

GAUNTLET_URL = "https://www.dropbox.com/scl/fi/u3bjyjlb474tskbjyzmpg/gauntlet_w_ref_summaries.parquet?rlkey=qjsz6htflg77monh2y5jb3kya&dl=1"

df = pd.read_parquet(GAUNTLET_URL).convert_dtypes()
df.info()
df.sample(n=7)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 19 entries, 0 to 18
Data columns (total 6 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   source_doc_filename  19 non-null     string
 1   source_doc_id        19 non-null     string
 2   source_doc_domain    19 non-null     string
 3   document_text        19 non-null     string
 4   summary              19 non-null     string
 5   summary_source       19 non-null     string
dtypes: string(6)
memory usage: 1.0 KB


source_doc_filename source_doc_id  \
8                         OCR_ML4HLecture02image_.txt  67f6cc9a-83c   
1   ASRnlp_law_lecture_week_2_v_2_c_transcription_...  016e8d29-288   
2   ASRnlp_law_lecture_week_3_part_1_v_2_c_transcr...  07af2cf9-15a   
16                       script_strangersonatrain.txt  9e6bfae4-7c2   
14                             script_findingnemo.txt  04a90337-527   
13  OCR_PAPER_Kandpal, Nieto, Jin - 2022 - Music E...  110b05be-f8d   
3   ASR-whisper-rpunctuated_Noam Chomsky, Fundam_1...  fed834b5-a04   

     source_doc_domain                                      document_text  \
8                  OCR  

Ezurich Lecture Machine Learning for Healthc...   
1                  ASR  I Just want to recap quickly what is already a...   
2                  ASR  I think we do reading as started. Thanks every...   
16              Script                     STRANGERS ON A TRAIN

     ...   
14              Script  ----------------------------------------------...   
13  OCR_academic_paper  

MUSIC ENHANCEMENT VIA IMAGE TRANSLATION AND ...   
3          ASR_cleaned  Well, I'd like to, in these two talks, I'd lik...   

                                              summary      summary_source  
8   The Ezurich Lecture on Machine Learning for He...  gpt-4-0125-preview  
1   The instructor begins the class by offering a ...  gpt-4-0125-preview  
2   The speaker addresses the adaptation to hybrid...  gpt-4-0125-preview  
16  "Strangers on a Train" is a suspenseful story ...  gpt-4-0125-preview  
14  The transcript details the plot of the 2003 an...  gpt-4-0125-preview  
13  Nikhil Kandpal, Oriol Nieto, Zeyu Jin, and the...  gpt-4-0125-preview  
3   The speaker explores the foundational aspects ...  gpt-4-0125-preview

let's encode the second half of each doc, to avoid giving away obvious clues like the titles etc at the beginning of a document


In [ ]:
import re

def second_half_of_text(text, split_by='word'):
    """
    # Example usage:
    text_by_word = "This is a sample string, with several words; and punctuation!"
    print(second_half_of_text(text_by_word, split_by='word'))

    text_by_line = "This is the first line.\n\nThis is the second line.\nThis is the third line.\nThis is the fourth line."
    print(second_half_of_text(text_by_line, split_by='line'))
    """
    # Define regex patterns for splitting
    if split_by == 'line':
        pattern = r'\n+'
    else:  # Default to splitting by word
        pattern = r'\s+'

    # Use regex to split based on the specified pattern
    elements = re.split(pattern, text)

    # Calculate midpoint and return the second half
    mid = len(elements) // 2
    if split_by == 'line':
        return '\n'.join(elements[mid:])
    else:
        return ' '.join(elements[mid:])


with several words; and punctuation!
This is the third line.
This is the fourth line.


In [ ]:
# compute 'second half' of each doc as text

df["text"] = df.document_text.apply(second_half_of_text, split_by='word')
df["text"].head()

0    acknowledging presence is up. I do not have th...
1    So when this is like the kind of classic workh...
2    right, but one is looted the other, but in ord...
3    somehow. It's just there, which means if we ev...
4    a general principle of computation. So Like in...
Name: text, dtype: object

In [ ]:
docs = df.text.to_list()
embeddings = model.encode(
    docs,
    batch_size=2,
    show_progress_bar=True,
    convert_to_tensor=True,
    normalize_embeddings=True,
)

Batches:   0%|          | 0/10 [00:00<?, ?it/s]

In [ ]:
print("shape of embeddings:", embeddings.shape)
embeddings

shape of embeddings: torch.Size([19, 768])


tensor([[ 0.0290, -0.0567, -0.0827,  ...,  0.0112,  0.0060,  0.0560],
        [ 0.0311, -0.0601, -0.0694,  ...,  0.0119, -0.0028,  0.0772],
        [ 0.0252, -0.0532, -0.0632,  ...,  0.0022, -0.0058,  0.0606],
        ...,
        [ 0.0365, -0.0177, -0.0940,  ..., -0.0283, -0.0046,  0.0375],
        [ 0.0524, -0.0479, -0.1166,  ...,  0.0024, -0.0087,  0.0404],
        [ 0.0321, -0.0502, -0.0823,  ..., -0.0290, -0.0640,  0.0139]],
       device='cuda:0')

In [ ]:
import torch
import torch.nn.functional as F

from torch import Tensor

#@markdown compute cosine similarity

def cos_sim(a: Tensor, b: Tensor) -> Tensor:
    """
    Computes the cosine similarity cos_sim(a[i], b[j]) for all i and j.

    source: sentence_transformers/util.py

    :return: Matrix with res[i][j]  = cos_sim(a[i], b[j])
    """
    if not isinstance(a, torch.Tensor):
        a = torch.tensor(a)

    if not isinstance(b, torch.Tensor):
        b = torch.tensor(b)

    if len(a.shape) == 1:
        a = a.unsqueeze(0)

    if len(b.shape) == 1:
        b = b.unsqueeze(0)

    a_norm = torch.nn.functional.normalize(a, p=2, dim=1)
    b_norm = torch.nn.functional.normalize(b, p=2, dim=1)
    return torch.mm(a_norm, b_norm.transpose(0, 1))


# Compute cosine similarity matrix efficiently
cosine_scores = cos_sim(embeddings, embeddings).cpu()

In [ ]:
import torch
import torch.nn.functional as F

# @title document pairs & similarity
top_n_pairs = 20  # @param {type:"slider", min:5, max:30, step:5}

df["doc_labels"] = df.apply(
    lambda row: row["source_doc_domain"] + " | " + row["source_doc_filename"], axis=1
)
docs = df.doc_labels.tolist()

cosine_scores_np = cosine_scores.cpu().numpy()

# Find the pairs with the highest cosine similarity scores, excluding self-comparisons
pairs = []
for i in range(len(cosine_scores_np) - 1):
    for j in range(i + 1, len(cosine_scores_np)):
        pairs.append({"index": [i, j], "score": cosine_scores_np[i][j]})

# Sort scores in decreasing order
pairs.sort(key=lambda x: x["score"], reverse=True)


def sp(text: str, max_chars: int = 45):
    return (
        text.strip() if len(str(text)) < max_chars else text[:max_chars].strip() + "..."
    )


def print_pairs(pairs, docs, title="Similar Document Pairs", top_n=10):
    """
    Prints specified number of top and bottom document pairs and their scores with improved formatting.
    """
    print(f"{title}:")
    print(f"{'Document 1':<50} {'Document 2':<50} {'Score':>10}")
    print("-" * 115)

    # Print top N pairs
    print(f"Top {top_n} most similar pairs:")
    for pair in pairs[:top_n]:
        i, j = pair["index"]
        print(f"{sp(docs[i]):<50} {sp(docs[j]):<50} {pair['score']:10.4f}")

    print("\n" + "-" * 115)

    # Print bottom N pairs
    print(f"Bottom {top_n} least similar pairs:")
    for pair in pairs[-top_n:]:
        i, j = pair["index"]
        print(f"{sp(docs[i]):<50} {sp(docs[j]):<50} {pair['score']:10.4f}")


# Display the top 10 and bottom 10 pairs with improved formatting
print(f"There are {len(pairs)} total pairs between all docs")
print(f"Results for:\t{model_name}\n\n")
print_pairs(
    pairs,
    docs,
    title="Document Similarity Pairs (domain | filename)",
    top_n=top_n_pairs,
)

There are 171 total pairs between all docs
Results for:	BEE-spoke-data/bert-plus-L8-v1.0-syntheticSTS-4k


Document Similarity Pairs (domain | filename):
Document 1                                         Document 2                                              Score
-------------------------------------------------------------------------------------------------------------------
Top 20 most similar pairs:
ASR | ASRnlp_law_lecture_week_1_v_2_c_transcr...   ASR | ASRnlp_law_lecture_week_2_v_2_c_transcr...       0.9513
ASR | ASRnlp_law_lecture_week_2_v_2_c_transcr...   ASR | ASRnlp_law_lecture_week_3_part_1_v_2_c_...       0.9504
ASR | ASRnlp_law_lecture_week_1_v_2_c_transcr...   ASR | ASRnlp_law_lecture_week_3_part_1_v_2_c_...       0.9494
ASR_cleaned | ASR-whisper-rpunctuated_Noam Ch...   ASR_cleaned | ASR-whisper-rpunctuated_Noam Ch...       0.9297
ASR | ASRnlp_law_lecture_week_3_part_1_v_2_c_...   ASR_cleaned | ASR-whisper-rpunctuated_Noam Ch...       0.9219
ASR | ASRnlp_law_lecture_

In [ ]:
model

SentenceTransformer(
  (0): Transformer({'max_seq_length': 4096, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 768, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
)

## bonus: summary embedding similarity


> what if we do (almost) the same thing but use the summaries (generated by GPT-4)?

In [ ]:
summaries = df.summary.to_list()
summary_embeddings = model.encode(
    summaries,
    batch_size=8,
    show_progress_bar=True,
    convert_to_tensor=True,
    normalize_embeddings=True,
)

Batches:   0%|          | 0/3 [00:00<?, ?it/s]

In [ ]:
summary_cosine_scores = cos_sim(summary_embeddings, summary_embeddings).cpu().numpy()

In [ ]:
# Find the pairs with the highest cosine similarity scores, excluding self-comparisons
summary_pairs = []
for i in range(len(summary_cosine_scores) - 1):
    for j in range(i + 1, len(summary_cosine_scores)):
        summary_pairs.append({"index": [i, j], "score": summary_cosine_scores[i][j]})

# Sort scores in decreasing order
summary_pairs.sort(key=lambda x: x["score"], reverse=True)
# Display the top 10 and bottom 10 pairs with improved formatting
print(f"There are {len(summary_pairs)} total pairs between all docs")
print(f"Results for:\t{model_name}\n\n")
print_pairs(
    summary_pairs,
    docs,
    title="Document-Summary Similarity (domain | filename)",
    top_n=10,
)

There are 171 total pairs between all docs
Results for:	BEE-spoke-data/bert-plus-L8-v1.0-syntheticSTS-4k


Document-Summary Similarity (domain | filename):
Document 1                                         Document 2                                              Score
-------------------------------------------------------------------------------------------------------------------
Top 10 most similar pairs:
OCR | OCR_ML4HLecture04RepresentationLearning...   OCR | OCR_ML4HLecture05-NLP.pptx_.txt                  0.9237
OCR | OCR_ML4HLecture02image_.txt                  OCR | OCR_ML4HLecture04RepresentationLearning...       0.9224
OCR | OCR_ML4HLecture02image_.txt                  OCR | OCR_ML4HLecture05-NLP.pptx_.txt                  0.8920
ASR_cleaned | ASR-whisper-rpunctuated_Noam Ch...   ASR_cleaned | ASR-whisper-rpunctuated_Noam Ch...       0.8811
OCR_academic_paper | OCR_PAPER_dall-e-2-annot...   OCR_academic_paper | OCR_PAPER_Hong et al. -...        0.8497
OCR | OCR_ML4HLecture02